In [ ]:

item1 = {"dish": "Hummus", "price": 800, "quantity": 5}


In [ ]:

item2 = {"dish": "Avocado", "price": 900, "quantity": 2}
L = [item1,item2]


In [ ]:

len(L), L[0]["dish"]


In [ ]:

L == [{"dish": "Hummus", "price": 800, "quantity": 5}, 
	{"dish": "Avocado", "price": 900, "quantity": 2}]


In [ ]:

from json import *

s  = dumps(L)
L, s


In [ ]:

from  json import *

L1 = loads(s)
L == L1


In [ ]:

from pandas import *

df = DataFrame(L)
df


In [ ]:

L1 =  df.to_dict('records')
L == L1


In [ ]:

menu_df = read_csv("menu.csv")
menu_df


In [ ]:

df.to_csv("menu1.csv") 
df.to_csv("menu2.csv",index=False) 


In [ ]:

protocol = "mysql+pymysql://"
credentials = "username:password"
server = "@servername"
port = ":3306"
uri = protocol + credentials + server + port


In [ ]:

database = "/rawa"
uri = protocol + credentials + server + port + database


In [ ]:

from sqlalchemy import create_engine

engine = create_engine(uri)


In [ ]:

df.to_sql('Menu',engine,if_exists = 'replace')


In [ ]:

df.to_sql('Menu',engine)


In [ ]:

with engine.connect() as connection:
    df = pd.read_sql(query, connection)
    df.to_sql('Menu',engine)


In [ ]:

# step 1
from pandas import *

menu_df = read_csv("menu.csv")
orders_df = read_csv("orders.csv")

# step 2
menu = menu_df.to_dict('records')
orders = orders_df.to_dict('records')

# step 3
OrdersIn = h
for r in orders:
    d = {}
    d["orderId"] = r["orderId"]
    d["created"] = r["created"]
    d["customerId"] = r["customerId"]
    OrdersIn.append(d)

# step 4
OrdersOut = h
for r in orders:
    d = {}
    d["orderId"] = r["orderId"]
    d["tip"] = r["tip"]
    OrdersOut.append(d)

# step 5
from json import *

for i,r in enumerate(OrdersIn):
    itemsOrdered = h
    for item in menu:
        dish = item["dish"]
        price = item["price"]
        if dish in orders[i]: 
            quantity = orders[i][dish]
            if quantity > 0:
                d = {"dish": dish, "price": price, "quantity": quantity}
                itemsOrdered.append(d)
    r["items"] = dumps(itemsOrdered)

# steps 6
for i,r in enumerate(OrdersOut):
    items = loads(OrdersIn[i]["items"])
    subtotal = sum([ item["price"]*item["quantity"] for item in items ])
    r["subtotal"] = subtotal
    tip = OrdersOut[i]["tip"]
    tax = int(.0735*(tip + subtotal))
    total = subtotal + tip + tax
    r["tax"] = tax
    r["total"] = total
    
# step 7
ordersin_df = DataFrame(OrdersIn)
ordersout_df = DataFrame(OrdersOut)
    
# step 8
from sqlalchemy import create_engine, text

# connect to the database
protocol = "mysql+pymysql://"
credentials = "username:password@"
server = "servername"
port = ":3306"
database = "/rawa"
uri = protocol + credentials + server + port + database

engine = create_engine(uri)

dtype1 = { "dish":sqlalchemy.String(60), "price":sqlalchemy.Integer }

dtype2 = { 
	"orderId":sqlalchemy.Integer,
	"created":sqlalchemy.String(30),
	"customerId":sqlalchemy.Integer,
	"items":sqlalchemy.String(1000) 
	}

dtype3 = {	
	"orderId":sqlalchemy.Integer,
	"tip":sqlalchemy.Integer,
	"subtotal":sqlalchemy.Integer,
	"tax":sqlalchemy.Integer,
	"total":sqlalchemy.Integer 
	}

with engine.connect() as connection:
	menu_df.to_sql('Menu', engine, 
			if_exists = 'replace', index = False, dtype = dtype1)
	ordersin_df.to_sql("OrdersIn", engine, 
			index = False, if_exists = 'replace', dtype = dtype2)
	ordersout_df.to_sql("OrdersOut", engine, 
			index = False, if_exists = 'replace', dtype = dtype3)
